In [1]:
%use klaxon
%use lets-plot

import java.net.*
import jetbrains.letsPlot.scale.*

val k = Klaxon()

val server = "http://localhost:6800"

In [2]:
data class FftSample(
    val index: Long, 
    val binCount: Int, 
    val samplesCount: Int, 
    val sampleRate: Float, 
    val magnitude: List<Double>,
    val phase: List<Double>,
    val frequency: List<Double>,
    val time: Long
)

data class Result(val offset: Long, val value: FftSample)

fun fftData(table: String, freqCutOff: Pair<Int, Int>): Map<String, List<Any>> {
    val data = URL("$server/table/$table/last?interval=10s").openStream().reader().readLines()
    .map { k.parse<Result>(it)!! }

    val timeShift = data.asSequence().map { it.value.time }.min() ?: 0
    val table = data.asSequence().map {v -> 
            v.value.magnitude.asSequence()
                .zip(v.value.frequency.asSequence())
                .filter { it.second >= freqCutOff.first && it.second <= freqCutOff.second}
                .map { arrayOf(
                        (v.value.time - timeShift) / 1e+6, // to milliseconds
                        it.second, 
                        it.first
                )}
        }
        .flatten()
        .toList() // this gives a list of tuples [ (time, freq, value), ... , (time, freq, value)]

    val dataFrame = mapOf(
        "time" to table.map { it[0] },
        "freq" to table.map { it[1] },
        "value" to table.map { it[2] }
    )    

    return dataFrame    
}


In [3]:
val df1 = fftData("fft-triangular", freqCutOff = 10 to 3800)
val df2 = fftData("fft-hamming", freqCutOff = 10 to 3800)

In [4]:

lets_plot(df1) {x = "time"; y = "freq"; fill = "value"} + 
    ggsize(1000, 600) + 
    geom_tile() + 
    scale_fill_gradient(low = "light_green", high = "red")
    

In [5]:

lets_plot(df2) {x = "time"; y = "freq"; fill = "value"} + 
    ggsize(1000, 600) + 
    geom_tile() + 
    scale_fill_gradient(low = "light_green", high = "red")
    